![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 13,14. <i>Korekta pisowni</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Współczesne programy typu CAT nie mogą obyć się bez korektora pisowni. Na bieżąco kontrolują one pisownię wyrazów po stronie docelowej, czyli tam, gdzie tłumacz wpisuje tłumaczenie. Jest to niezwykle istotne w sytuacji, gdy język docelowy nie jest dla tłumacza językiem ojczystym. Co więcej, badania wykazują, iż korekta pisowni wydatnie zmniejsza liczbę błędów w każdych scenariuszach.

Co poprawia korekta pisowni? Słowa. Tylko lub aż słowa. Program dokonujący korekty pisowni przegląda tekst słowo po słowie i sprawdza, czy należy ono do słownika. Jeśli nie, sygnalizowany jest błąd oraz, jeśli to możliwe, podawane sugestie poprawy. Co istotne, korektor pisowni nie zajmuje się szeregiem błędów, które mieszczą się w dziedzinie korekty gramatycznej, w tym:
* interpunkcją
* powtórzeniami wyrazów
* stylistyką.

Aby zaimplementować korektor pisowni bez wątpienia potrzebny jest słownik. Skorzystajmy ze słownika, który znajdziemy w folderze data, pochodzącego z narzędzia Hunspell. Jest on spakowany - użyjmy techniki czytania z archiwum zip bez rozpakowywania. Poniższy kod wypisze fragment ze środka słownika.

In [2]:
from zipfile import ZipFile

with ZipFile('data/hunspell_pl.zip') as zipped_dictionary:
    with zipped_dictionary.open('hunspell_pl.txt') as dictionary_file:
        count = 0
        for line_bytes in dictionary_file:
            count += 1
            if count >= 100000 and count <= 100020:
                line = line_bytes.decode('utf-8')
                print(line.rstrip())

kalecząc
kaledonidy
kaledoński
kalefaktor
kalejdofon
kalejdoskop
kalejdoskopowość
kalejdoskopowy
kaleka
kaleki
kalema
kalendarium
kalendarz
kalendarzowy
kalendarzyk
kalendy
kalenica
kalenicowy
kalepin
kalesonki
kalesony


Miejmy na uwadze, że powyższy słownik zawiera tylko formy podstawowe słowa, np. zawiera słowo "kalendarz", ale nie zawiera "kalendarze", "kalendarza", "kalendarzy" itp. 

Algorytm korekty pisowni na podstawie słownika powinien działać według następujących kroków:
1. Wczytanie słownika do zbioru (set)
2. Podział tekstu do korekty na słowa (podział po spacji)
3. Dla każdego słowa wypisać, czy jest ono poprawne (znajduje się w słowniku) czy nie.

### Ćwiczenie 1: Zaimplementuj podstawowy algorytm korekty pisowni według powyższych wytycznych.

In [33]:
from zipfile import ZipFile
def correct_text(text):
    text = text.rstrip().split(" ")
    isCorrect = [False] * len(text)
    with ZipFile('data/hunspell_pl.zip') as zipped_dictionary:
        with zipped_dictionary.open('hunspell_pl.txt') as dictionary_file:
                for line_bytes in dictionary_file:
                    bline = line_bytes.decode('utf-8').rstrip()
                    i = 0
                    for _ in range(len(text)):
                        if bline == text[i]:
                            isCorrect[i] = True
                        i += 1
                        
    return isCorrect

correct_text("Nadia jestr super")

[True, False, True]

To jednak oczywiście nie wszystko. Do tej pory mamy funkcjonalność sygnalizowania słów błędnych, ale każdy dobry korektor pisowni potrafi podać sugestie poprawek. W tym celu musimy stawić czoła następującemu problemowi - wygenerowanie listy słów podobnych do danego słowa błędnego, które znajdują się w słowniku.

W pierwszej kolejności musimy zdefiniować podobieństwo między wyrazami. Posłuży do tego dobrze nam znana odległość Levenshteina - wyrazy podobne to takie, dla których dystans Levenshteina jest niewielki (np. równy 1 lub 2). Teraz brakuje tylko algorytmu wyszukiwania wyrazów w danym słowniku, które znajdują się niedaleko (w sensie Levenshteina) danego błędnego słowa.

Rozważmy następujący algorytm: dla danego słownika $D$ i błędnego słowa $w \notin D$:
1. Wygeneruj zbiór $L_1(w)$ wszystkich słów, których odległość Levenshteina od $w$ wynosi 1.
2. Wyznacz zbiór $S_1(w)=L_1(w) \cap D$
3. Wyznacz zbiór $L_2(w)=\bigcup_{v \in L_1(w)} L_1(v)$
4. Wyznacz zbiór $S_2(w)=L_2(w) \cap D$
5. Zwróć jako listę sugestii: $S_1 \cup S_2$

### Ćwiczenie 2: Napisz funkcję do generowania zbioru $L_1(w)$ - wszystkich słów znajdujących się w odległości Levenshteina 1 od danego słowa w.

In [62]:
from zipfile import ZipFile

def L1(w):
    w.lower()
    word_len = len(w)
    words = set()
    with ZipFile('data/hunspell_pl.zip') as zipped_dictionary:
        with zipped_dictionary.open('hunspell_pl.txt') as dictionary_file:
                for line_bytes in dictionary_file:
                    cost = 0
                    bline = line_bytes.decode('utf-8').rstrip().lower()
                    if len(bline) < word_len - 1 or len(bline) > word_len + 1:
                        continue
                    elif len(bline) == word_len:
                        for i in range(word_len):
                            if cost > 1:
                                continue
                            if w[i] != bline[i]:
                                cost += 1
                        if cost == 1:
                            words.add(bline)
                    else:
                        if w in bline:
                            words.add(bline)
                        
    return words

L1("woda")

{'coda',
 'doda',
 'koda',
 'moda',
 'roda',
 'soda',
 'wada',
 'weda',
 'wodan',
 'wola',
 'wota',
 'woza',
 'woła',
 'wóda',
 'węda'}

### Ćwiczenie 3: Napisz funkcję do generowania sugestii poprawek dla danego słowa według opisanego wcześniej algorytmu.

In [69]:
def generate_suggestions(w):
    S1 = L1(w)
    S2 = set()
    for word in S1:
        sugestions = L1(word)
        for sug in sugestions:
            S2.add(sug)
    return set.union(S1, S2).difference({w})

generate_suggestions("teść")

{'jeść', 'ujeść', 'zjeść'}